# MEAM 5170 Final Project 

Initialization

**Re-run this block anytime you make changes**

In [ ]:
%matplotlib inline

"""
Simulate quadrotor
"""

import numpy as np
from math import sin, cos, pi
import matplotlib.pyplot as plt
import importlib

from quad_sim_pendulum import simulate_quadrotor

# Need to reload the module to use the latest code
from quadrotor_with_pendulum import QuadrotorPendulum
from animation import Animation
from world import Obstacles

from trajectory_optimizer_casadi import optimize_trajectory

/shared-libs/python3.8/py/lib/python3.8/site-packages/scipy/__init__.py:155: UserWarning: A NumPy version >=1.18.5 and <1.26.0 is required for this version of SciPy (detected version 1.17.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


## Quadrotor with MPC


In [ ]:
# Weights of LQR cost
R = np.eye(2)
Q = np.diag([10, 10, 1, 1, 1, 1, 1, 1])
Qf = Q

# End time of the simulation
tf = 10

x_f = np.array([4, 2, 0, 0, 0, 0, 0, 0])

# Construct our quadrotor controller 
quadrotor = QuadrotorPendulum(Q, R, Qf, x_f)

# Set quadrotor's initial state and simulate
x0 = np.array([1, 1, 0, 0, 1, 1, 0, 0])
x, u, t = simulate_quadrotor(x0, tf, x_f, quadrotor)

obstacles = Obstacles("./configs/world.yaml")
anime = Animation(obstacles, quadrotor)
anime.set_trajectory(x)
print('x = ', x, '\n')
print('u =', u)

anime.animate()

x =  [[ 1.00000000e+00  1.00000000e+00  0.00000000e+00 ...  1.00000000e+00
   0.00000000e+00  0.00000000e+00]
 [ 1.01000000e+00  1.01000000e+00  0.00000000e+00 ...  1.00068642e+00
  -9.21675242e-02  0.00000000e+00]
 [ 1.02000000e+00  1.02000686e+00 -9.21675242e-04 ...  1.00129938e+00
  -1.63525656e-01  0.00000000e+00]
 ...
 [ 4.00303121e+00  2.03722185e+00  1.85566310e-03 ... -2.15012119e-03
  -3.23275757e-03 -3.66003676e-03]
 [ 4.00302116e+00  2.03720035e+00  1.82333552e-03 ... -2.39438612e-03
  -3.30720961e-03 -3.73539266e-03]
 [ 4.00300936e+00  2.03717641e+00  1.79026343e-03 ... -2.63697621e-03
  -3.37874112e-03 -3.80755300e-03]] 

u = [[ 0.          0.        ]
 [15.41018789 14.79573773]
 [15.32980495 14.85408408]
 ...
 [14.96339399 14.96287825]
 [14.96363393 14.96313758]
 [14.96387482 14.96339794]]


## Quadrotor with LQR

In [ ]:
# Weights of LQR cost
R = np.eye(2)
Q = np.diag([10, 10, 1, 1, 1, 1, 1, 1])
Qf = Q

# End time of the simulation
tf = 10

x_f = np.array([4, 2, 0, 0, 0, 0, 0, 0])

# Construct our quadrotor controller 
quadrotor = QuadrotorPendulum(Q, R, Qf, x_f)

# Set quadrotor's initial state and simulate
x0 = np.array([2, 2, 0, 0, 1, 1, 0, 0])
x, u, t = simulate_quadrotor(x0, tf, x_f, quadrotor, False)

obstacles = Obstacles("./configs/world.yaml")
anime = Animation(obstacles, quadrotor)
anime.set_trajectory(x)
print('x = ', x, '\n')
print('u =', u)

anime.animate()

x =  [[ 2.00000000e+00  2.00000000e+00  0.00000000e+00 ...  1.00000000e+00
   0.00000000e+00  0.00000000e+00]
 [ 2.01000000e+00  2.01000000e+00  0.00000000e+00 ...  9.82101268e-01
  -1.42717104e+00  0.00000000e+00]
 [ 2.02000000e+00  2.01982101e+00 -1.42717104e-02 ...  9.64373829e-01
  -2.35609288e+00  0.00000000e+00]
 ...
 [ 5.00000011e+00  1.99990320e+00 -3.90693732e-07 ... -1.02985816e-04
   3.07921831e-08  1.88641526e-07]
 [ 5.00000010e+00  1.99990217e+00 -3.90385811e-07 ... -9.96995154e-05
   6.40858160e-08  2.20658921e-07]
 [ 5.00000009e+00  1.99990117e+00 -3.89744952e-07 ... -9.64566829e-05
   9.62934039e-08  2.51492394e-07]] 

u = [[ 0.          0.        ]
 [17.07242694  7.55795336]
 [15.43729032  9.24447801]
 ...
 [15.00049939 15.00049962]
 [15.00049283 15.00049306]
 [15.00048632 15.00048653]]


## Trajectory Optimization with PyDrake

In [ ]:
# Weights of LQR cost
R = np.eye(2)
Q = np.diag([10, 10, 1, 1, 1, 1, 1, 1])
Qf = Q

# End time of the simulation
tf = 10
max_iter = 10

# Set quadrotor's initial state and simulate
t_i = np.load('initial_guesses/t.npy')
u_i = np.load('initial_guesses/u.npy')
x_i = np.load('initial_guesses/x.npy')
N = x_i.shape[0]
t_step = t_i[1] - t_i[0]
x_0 = x_i[0]
x_f = x_i[-1]

print('t_i =', t_i)
print('u_i =', u_i)
print('x_i =', x_i)
print('N =', N)
print('t_step =', t_step)

initial_trajectory = {
    'state': x_i,
    'input': u_i
}

# Construct our quadrotor controller 
quadrotor = QuadrotorPendulum(Q, R, Qf, x_f)

obstacles = Obstacles("./configs/world.yaml")
traj_opt = TrajectoryOptimizer(quadrotor)

x, u, t = traj_opt.simulate_quadrotor(x_0, tf, x_f, N, t_step, obstacles, max_iter, initial_trajectory)

anime = Animation(obstacles, quadrotor)
anime.set_trajectory(x)
print('x = ', x, '\n')
print('u =', u)

anime.animate()

t_i = [ 0.   0.5  1.   1.5  2.   2.5  3.   3.5  4.   4.5  5.   5.5  6.   6.5
  7.   7.5  8.   8.5  9.   9.5 10.  10.5 11.  11.5 12.  12.5 13.  13.5
 14.  14.5 15.  15.5 16.  16.5 17.  17.5 18.  18.5 19.  19.5 20.  20.5
 21.  21.5 22.  22.5 23.  23.5 24.  24.5 25.  25.5 26.  26.5 27.  27.5
 28.  28.5 29.  29.5 30.  30.5 31.  31.5 32.  32.5 33.  33.5 34.  34.5
 35.  35.5 36.  36.5 37.  37.5 38.  38.5 39.  39.5 40.  40.5 41.  41.5
 42.  42.5 43.  43.5 44.  44.5 45.  45.5 46.  46.5 47.  47.5 48.  48.5
 49.  49.5 50.  50.5 51.  51.5 52.  52.5 53.  53.5 54.  54.5 55.  55.5
 56.  56.5 57.  57.5 58.  58.5 59.  59.5 60.  60.5 61.  61.5 62.  62.5
 63. ]
u_i = [[ 0.          0.        ]
 [15.04388646 14.6323487 ]
 [13.52569482 13.55293606]
 [16.98021734 16.60165535]
 [15.60258106 15.7365986 ]
 [15.24649983 15.27122517]
 [15.02665122 15.04137797]
 [15.0337643  15.02624264]
 [15.05057076 15.04454679]
 [15.02188301 15.02193574]
 [14.99337669 14.99495898]
 [14.98502463 14.98555896]
 [14.98951797 14.9

NameError: name 'TrajectoryOptimizer' is not defined

## Trajectory Optimization with SciPy

In [ ]:
# Weights of LQR cost
R = np.eye(2)
Q = np.diag([10, 10, 1, 1, 1, 1, 1, 1])
Qf = Q

# Get initial trajectory
u_i = np.load('initial_guesses/u_short1.npy')
u_i = u_i[1:]
x_i = np.load('initial_guesses/x_short.npy')
N = x_i.shape[0]
dt = 0.3
x_f = x_i[-1]

print('u_i =', u_i)
print('u_i size =', u_i.shape)
print('x_i =', x_i)
print('x_i size =', x_i.shape)
print('N =', N)
print('dt =', dt)

initial_trajectory = {
    'state': x_i,
    'input': u_i
}

# Construct our quadrotor controller 
quadrotor = QuadrotorPendulum(Q, R, Qf, x_f, lb=0.3, l1=0.5)

obstacles = Obstacles("./configs/world.yaml")

# tuning_params = {'goal_param': 0.1, 'barrier_param': 100000, 'lambda_param': 10, 'dist_param': 0.001,
#                 'vel_param': 1}

# opt_params = {'max_iter': 500, 'acceptable_tol': 1e-2, 'acceptable_constr_viol_tol': 1e-4}

# x_opt, u_opt, success = optimize_trajectory(quadrotor, obstacles, N, dt, initial_trajectory, 
#                                             tuning_params, opt_params)

# if success:
#     print('x = ', x_opt, '\n')
#     print('u =', u_opt)
#     print("Solution found")
# else:
#     print("No solution found")

u_i = [[10.79040001 11.64516864]
 [21.62236003 17.2515159 ]
 [14.3478905  12.99971592]
 [15.31560687 15.61198811]
 [21.75840376 20.17063921]
 [16.46583119 16.58588376]
 [14.46284639 14.59157457]
 [14.12288363 14.14273844]
 [14.59620726 14.5545048 ]
 [14.66735276 14.68365071]
 [14.70535491 14.72619135]
 [14.88303223 14.8842225 ]
 [15.02267628 15.0194776 ]
 [15.07985639 15.07666051]
 [15.09188534 15.08884712]
 [15.07692651 15.07572576]
 [15.05251995 15.05299317]
 [15.03343349 15.03434511]
 [15.02283942 15.02346906]
 [15.01739243 15.01761142]
 [15.01364854 15.01357632]
 [15.0099162  15.00973731]
 [15.00598089 15.00583782]
 [15.00239696 15.00234052]
 [14.99975257 14.99976366]
 [14.99825459 14.99829169]
 [14.9977261  14.99775753]
 [14.99781038 14.99782404]
 [14.9981676  14.99816633]
 [14.99857453 14.99856686]
 [14.99893146 14.9989245 ]
 [14.99921941 14.99921615]
 [14.99945137 14.99945142]
 [14.99964152 14.9996431 ]
 [14.99979548 14.999797  ]
 [14.99991306 14.99991383]
 [14.99999421 14.99999

### NLP without Swing Motion

In [ ]:
tuning_params = {'goal_param': 10, 'barrier_param': 100, 'lambda_param': 10, 'dist_param': 1,
                'vel_param': 3}

opt_params = {'max_iter': 500, 'acceptable_tol': 1e-2, 'acceptable_constr_viol_tol': 1e-4}

x_opt, u_opt, success = optimize_trajectory(quadrotor, obstacles, N, dt, initial_trajectory, 
                                            tuning_params, opt_params)

np.save('x_NLP_no_swing.npy', x_opt)

anime = Animation(obstacles, quadrotor)
anime.set_trajectory(x_opt)
anime.animate()

B shape = @1=(zeros(8x2)[4] = 0.0017844), @2=((@1[12] = @1[4])[5] = 0.333341), (0.3*(((((@2[13] = @2[5])[6] = -10)[14] = 10)[7] = -0.00504459)[15] = -0.00504459))
boundary = [0, 0, 8, 4]
boxes = [[3.9, -0.4, 4.1, 1.8], [3.9, 2.2, 4.1, 4.4]]

******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit https://github.com/coin-or/Ipopt
******************************************************************************

This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:     8520
Number of nonzeros in inequality constraint Jacobian.:      674
Number of nonzeros in Lagrangian Hessian.............:     1352

Total number of variables............................:     1128
                     variables with only lo

### NLP with Swinging Motion 1

In [ ]:
tuning_params = {'goal_param': 10, 'barrier_param': 100, 'lambda_param': 10, 'dist_param': 1,
                'vel_param': 3}

opt_params = {'max_iter': 500, 'acceptable_tol': 1e-2, 'acceptable_constr_viol_tol': 1e-4}

x_opt, u_opt, success = optimize_trajectory(quadrotor, obstacles, N, dt, initial_trajectory, 
                                            tuning_params, opt_params)

np.save('x_NLP_swing_1.npy', x_opt)

if success:
    print("Solution found")
else:
    print("No solution found")

anime = Animation(obstacles, quadrotor)
anime.set_trajectory(x_opt)
anime.animate()

B shape = @1=(zeros(8x2)[4] = 0.0017844), @2=((@1[12] = @1[4])[5] = 0.333341), (0.3*(((((@2[13] = @2[5])[6] = -10)[14] = 10)[7] = -0.00504459)[15] = -0.00504459))
boundary = [0, 0, 8, 4]
boxes = [[3.9, -0.4, 4.1, 1.8], [3.9, 2.2, 4.1, 4.4]]

******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit https://github.com/coin-or/Ipopt
******************************************************************************

This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:     8520
Number of nonzeros in inequality constraint Jacobian.:      674
Number of nonzeros in Lagrangian Hessian.............:     1912

Total number of variables............................:     1128
                     variables with only lo

### NLP with Swinging Motion 2

In [ ]:
 tuning_params = {'goal_param': 100, 'barrier_param': 100, 'lambda_param': 100, 'dist_param': 0.001,
                 'vel_param': 0.01}

opt_params = {'max_iter': 500, 'acceptable_tol': 1e-2, 'acceptable_constr_viol_tol': 1e-4}

x_opt, u_opt, success = optimize_trajectory(quadrotor, obstacles, N, dt, initial_trajectory, 
                                            tuning_params, opt_params)

np.save('x_NLP_swing_2.npy', x_opt)

if success:
    print("Solution found")
else:
    print("No solution found")

anime = Animation(obstacles, quadrotor)
anime.set_trajectory(x_opt)
anime.animate()

B shape = @1=(zeros(8x2)[4] = 0.0017844), @2=((@1[12] = @1[4])[5] = 0.333341), (0.3*(((((@2[13] = @2[5])[6] = -10)[14] = 10)[7] = -0.00504459)[15] = -0.00504459))
boundary = [0, 0, 8, 4]
boxes = [[3.9, -0.4, 4.1, 1.8], [3.9, 2.2, 4.1, 4.4]]
This is Ipopt version 3.14.11, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:     8520
Number of nonzeros in inequality constraint Jacobian.:      674
Number of nonzeros in Lagrangian Hessian.............:     1912

Total number of variables............................:     1128
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      904
Total number of inequality constraints...............:      674
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=bc24b42c-2384-48c3-b1e2-6f6c0205f5f5' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>